In [16]:
# Requirements:
!pip install langchain unstructured[all-docs] pydantic lxml openai chromadb tiktoken pytesseract langchain_google_genai
!pip install langchain-huggingface transformers torch
!pip install -U langchain-community
!pip install pytesseract

!apt-get install -y poppler-utils
!apt-get install -y tesseract-ocr

!pip install google-generativeai

!pip install langchain-google-community[drive]
!pip install --upgrade google-api-python-client google-auth-httplib2 google-auth-oauthlib


  Using cached google_ai_generativelanguage-0.6.17-py3-none-any.whl.metadata (9.8 kB)
Using cached google_ai_generativelanguage-0.6.17-py3-none-any.whl (1.4 MB)
  Attempting uninstall: google-ai-generativelanguage
    Found existing installation: google-ai-generativelanguage 0.6.15
    Uninstalling google-ai-generativelanguage-0.6.15:
      Successfully uninstalled google-ai-generativelanguage-0.6.15
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-generativeai 0.8.4 requires google-ai-generativelanguage==0.6.15, but you have google-ai-generativelanguage 0.6.17 which is incompatible.


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
poppler-utils is already the newest version (22.02.0-2ubuntu0.7).
0 upgraded, 0 newly installed, 0 to remove and 34 not upgraded.
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
tesseract-ocr is already the newest version (4.1.1-2.1build1).
0 upgraded, 0 newly installed, 0 to remove and 34 not upgraded.
  Using cached google_ai_generativelanguage-0.6.15-py3-none-any.whl.metadata (5.7 kB)
Using cached google_ai_generativelanguage-0.6.15-py3-none-any.whl (1.3 MB)
  Attempting uninstall: google-ai-generativelanguage
    Found existing installation: google-ai-generativelanguage 0.6.17
    Uninstalling google-ai-generativelanguage-0.6.17:
      Successfully uninstalled google-ai-generativelanguage-0.6.17
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the fo

In [17]:
import os
import io
from google.oauth2 import service_account
from googleapiclient.discovery import build
from googleapiclient.http import MediaIoBaseDownload
from unstructured.partition.auto import partition
import traceback # Import traceback for more detailed error info (optional)

# --------- SETTINGS ---------
SERVICE_ACCOUNT_FILE = "/content/steady-citron-457407-q7-5c09ed11e0d4.json"
FOLDER_ID = "1LyiyENXg85q-uLQjlddNEeRsi6bgKdTq" # misc documents
# Removed VALID_EXTENSIONS to attempt partitioning all files
DOWNLOAD_TMP_DIR = "/content/drive_downloads"
EXTRACTED_FIGURES_BASE_DIR = os.path.join(os.getcwd(), "figures") # Base directory for saving figures

# Ensure download and figures base directories exist
os.makedirs(DOWNLOAD_TMP_DIR, exist_ok=True)
os.makedirs(EXTRACTED_FIGURES_BASE_DIR, exist_ok=True)


# --------- AUTH ---------
try:
    creds = service_account.Credentials.from_service_account_file(SERVICE_ACCOUNT_FILE)
    drive_service = build('drive', 'v3', credentials=creds)
    print("Google Drive authentication successful.")
except Exception as e:
    print(f"Error during Google Drive authentication: {e}")
    print("Please check your service account file path and ensure it's valid.")
    # In a real application, you might want to exit or handle this differently
    # For this script, we'll let it continue but no files will be loaded.
    drive_service = None


# --------- GET FILES FROM FOLDER ---------
def get_files_from_folder(folder_id):
    """Recursively fetches files from a Google Drive folder."""
    all_files = []
    if drive_service is None:
        print("Skipping file fetch due to authentication failure.")
        return []

    print(f"Fetching files from Google Drive folder ID: {folder_id}")

    def _recursive_fetch(current_folder_id):
        query = f"'{current_folder_id}' in parents and trashed=false"
        try:
            results = drive_service.files().list(q=query, fields="files(id, name, mimeType)").execute()
            files = results.get('files', [])

            for file in files:
                # print(f"Found item: {file['name']} ({file['mimeType']})") # Optional: print all items found
                if file["mimeType"] == "application/vnd.google-apps.folder":
                    # print(f"Entering subfolder: {file['name']}")
                    _recursive_fetch(file["id"])  # 📁 Recurse into subfolder
                else:
                    all_files.append(file)
            # print(f"Fetched {len(files)} items from folder ID: {current_folder_id}")
        except Exception as e:
            print(f"Error fetching files from folder ID {current_folder_id}: {e}")
            # traceback.print_exc() # Optional: print traceback for fetching errors


    _recursive_fetch(folder_id)
    print(f"Finished fetching files. Found a total of {len(all_files)} files.")
    return all_files

# --------- MAIN LOAD LOGIC ---------
def load_and_partition_drive_documents(folder_id, download_dir, figures_base_dir):
    """
    Loads all files from a Google Drive folder and attempts to partition them.
    Continues execution even if partitioning a single file fails.

    Args:
        folder_id: The ID of the Google Drive folder.
        download_dir: Directory to temporarily download files.
        figures_base_dir: Base directory to save extracted figures/images.

    Returns:
        A list of dictionaries, each containing filename and extracted elements
        for successfully processed files.
    """
    processed_docs = []
    files = get_files_from_folder(folder_id)

    if not files:
        print("No files to process.")
        return []

    for file in files:
        file_id = file["id"]
        name = file["name"]

        # Attempt to process all files, removing the VALID_EXTENSIONS check
        # if name.startswith("~$") or not any(name.endswith(ext) for ext in VALID_EXTENSIONS):
        #     print(f"Skipping file: {name}")
        #     continue

        local_path = os.path.join(download_dir, name)
        # Create a specific output directory for figures from this file
        output_figures_path = os.path.join(figures_base_dir, os.path.splitext(name)[0])
        os.makedirs(output_figures_path, exist_ok=True)

        print(f"\nAttempting to process: {name}")

        try:
            request = drive_service.files().get_media(fileId=file_id)

            # Download file to temporary directory
            with io.FileIO(local_path, "wb") as fh:
                downloader = MediaIoBaseDownload(fh, request)
                done = False
                while not done:
                    status = downloader.next_chunk()
                    # print(f"Download progress for {name}: {status[0].progress() * 100:.0f}%") # Optional: progress
                    _, done = status


            print(f"Downloaded: {name} to {local_path}")

            # Extract elements using Unstructured's partition()
            # The try...except block handles failures here
            elements = partition(
                filename=local_path,
                strategy="hi_res", # Using hi_res as requested in the snippet
                # extract_images_in_pdf=True, # Deprecated, use extract_image_block_types
                languages=["eng"], # Specify language for OCR
                extract_image_block_to_payload = True,
                # Parameters for extracting images and tables to a directory
                extract_image_block_types=["Image", "Table"],
                infer_table_structure=True, # Infer table structure
                image_output_dir_path=output_figures_path # Directory to save extracted images/tables
            )

            processed_docs.append({"filename": name, "elements": elements, "extracted_figures_dir": output_figures_path})
            print(f"✅ Successfully loaded and partitioned: {name} ({len(elements)} elements found)")
            # Optional: List extracted files in the figures directory
            extracted_files = os.listdir(output_figures_path)
            if extracted_files:
                 print(f"   Extracted figures/tables saved to: {output_figures_path} ({len(extracted_files)} files)")
            else:
                 print(f"   No figures/tables extracted to: {output_figures_path}")


        except Exception as e:
            # This block ensures that if partition fails, the program continues
            print(f"❌ Failed to partition {name}: {e}")
            # traceback.print_exc() # Optional: print detailed traceback for partitioning errors
            # Clean up the created figures directory if nothing was saved
            if os.path.exists(output_figures_path) and not os.listdir(output_figures_path):
                 os.rmdir(output_figures_path)


        finally:
            # Clean up the downloaded file after processing attempt
            if os.path.exists(local_path):
                os.remove(local_path)


    return processed_docs

# --------- RUN ---------
# This will load and attempt to partition all files in the specified folder.
# Failures for individual files will be reported, but the script will continue.

documents = load_and_partition_drive_documents(FOLDER_ID, DOWNLOAD_TMP_DIR, EXTRACTED_FIGURES_BASE_DIR)
print(f"\n🎉 Done processing files. Successfully partitioned {len(documents)} documents.")
print(f"Extracted figures and tables are saved in subdirectories within: {EXTRACTED_FIGURES_BASE_DIR}")

# You can now work with the 'documents' list, which contains the filename
# and extracted elements for each file that was successfully partitioned.
# for doc_info in documents:
#     print(f"\n--- Contents of {doc_info['filename']} ---")
#     # print(f"Extracted figures saved in: {doc_info['extracted_figures_dir']}")
#     # for element in doc_info['elements']:
#     #    print(element) # Print or process the elements

Google Drive authentication successful.
Fetching files from Google Drive folder ID: 1LyiyENXg85q-uLQjlddNEeRsi6bgKdTq
Finished fetching files. Found a total of 12 files.

Attempting to process: 6-CNN.pptx
Downloaded: 6-CNN.pptx to /content/drive_downloads/6-CNN.pptx
✅ Successfully loaded and partitioned: 6-CNN.pptx (191 elements found)
   No figures/tables extracted to: /content/figures/6-CNN

Attempting to process: Screenshot_20250119_225205_YouTube.jpg
Downloaded: Screenshot_20250119_225205_YouTube.jpg to /content/drive_downloads/Screenshot_20250119_225205_YouTube.jpg
✅ Successfully loaded and partitioned: Screenshot_20250119_225205_YouTube.jpg (4 elements found)
   No figures/tables extracted to: /content/figures/Screenshot_20250119_225205_YouTube

Attempting to process: vulnerable_echoserver.c
Downloaded: vulnerable_echoserver.c to /content/drive_downloads/vulnerable_echoserver.c
✅ Successfully loaded and partitioned: vulnerable_echoserver.c (22 elements found)
   No figures/tables

In [18]:
#documents = load_and_partition_drive_documents(FOLDER_ID, DOWNLOAD_TMP_DIR, EXTRACTED_FIGURES_BASE_DIR)

**Save the Images locally**

In [19]:
import os
import base64
from io import BytesIO
from PIL import Image as PILImage
from unstructured.documents.elements import Image as UnstructuredImage

def save_unstructured_images(documents, output_dir="saved_images"):
    """
    Decode and save each UnstructuredImage element's Base64 payload
    into the specified output directory as individual image files.
    """
    # 1. Create output directory (and any parents) if missing
    os.makedirs(output_dir, exist_ok=True)

    image_count = 0
    for doc in documents:
        for element in doc.get("elements", []):
            if isinstance(element, UnstructuredImage):
                # 2. Extract Base64 payload from metadata
                data = element.to_dict().get("metadata", {}).get("image_base64", "")
                if not data:
                    continue
                # 3. Strip off data URI header if present
                if "," in data:
                    data = data.split(",", 1)[1]
                # 4. Decode Base64 to bytes
                raw_bytes = base64.b64decode(data)
                # 5. Wrap in BytesIO buffer
                buffer = BytesIO(raw_bytes)
                buffer.seek(0)
                # 6. Load as PIL Image
                pil_img = PILImage.open(buffer)
                pil_img.load()  # optional: ensure full read

                # 7. Choose a filename and save
                filename = f"image_{image_count}.png"
                filepath = os.path.join(output_dir, filename)
                pil_img.save(filepath)

                print(f"Saved image #{image_count} to {filepath}")
                image_count += 1

# Example usage:



In [20]:
save_unstructured_images(documents, output_dir="my_extracted_images")

Saved image #0 to my_extracted_images/image_0.png
Saved image #1 to my_extracted_images/image_1.png
Saved image #2 to my_extracted_images/image_2.png
Saved image #3 to my_extracted_images/image_3.png
Saved image #4 to my_extracted_images/image_4.png
Saved image #5 to my_extracted_images/image_5.png
Saved image #6 to my_extracted_images/image_6.png
Saved image #7 to my_extracted_images/image_7.png
Saved image #8 to my_extracted_images/image_8.png
Saved image #9 to my_extracted_images/image_9.png
Saved image #10 to my_extracted_images/image_10.png
Saved image #11 to my_extracted_images/image_11.png
Saved image #12 to my_extracted_images/image_12.png
Saved image #13 to my_extracted_images/image_13.png
Saved image #14 to my_extracted_images/image_14.png
Saved image #15 to my_extracted_images/image_15.png
Saved image #16 to my_extracted_images/image_16.png
Saved image #17 to my_extracted_images/image_17.png
Saved image #18 to my_extracted_images/image_18.png
Saved image #19 to my_extracted_

In [24]:
!pip install langchain-text-splitters


In [27]:
import base64
from io import BytesIO
from typing import Any, Dict, List, Tuple

import torch
from PIL import Image as PILImage
from transformers import BlipProcessor, BlipForConditionalGeneration
from unstructured.documents.elements import Image as UnstructuredImage, Table as UnstructuredTable

def generate_captions_from_memory(
    documents: List[Dict[str, Any]],
    model_name: str = "Salesforce/blip-image-captioning-base",
    device: str = None,
) -> Tuple[Dict[str, str], Dict[str, str]]:
    """
    Iterate all Image and Table elements in `documents`, decode their in‑payload Base64,
    and generate captions via BLIP (in memory, no disk I/O).

    Args:
        documents: list of dicts, each with key "elements": List[Element]
        model_name: HF model to load
        device: 'cuda' or 'cpu' (auto‑chosen if None)

    Returns:
        (image_captions, table_captions):
            image_captions: Dict[element_id, caption]
            table_captions: Dict[element_id, caption]
    """
    # Device setup
    device = device or ("cuda" if torch.cuda.is_available() else "cpu")

    # Load BLIP processor & model once
    processor = BlipProcessor.from_pretrained(model_name)
    model = BlipForConditionalGeneration.from_pretrained(model_name).to(device)

    image_captions: Dict[str, str] = {}
    table_captions: Dict[str, str] = {}
    img_count = 0
    tbl_count = 0

    for doc in documents:
        for el in doc.get("elements", []):
            # Only process images or tables
            if isinstance(el, UnstructuredImage) or isinstance(el, UnstructuredTable):
                # 1) Extract Base64 from metadata
                md = el.to_dict().get("metadata", {})
                b64 = md.get("image_base64", "")
                if not b64:
                    continue
                if "," in b64:
                    b64 = b64.split(",", 1)[1]

                # 2) Decode & load PIL image
                raw = base64.b64decode(b64)
                buf = BytesIO(raw)
                buf.seek(0)
                img = PILImage.open(buf).convert("RGB")

                # 3) Generate caption
                inputs = processor(images=img, return_tensors="pt").to(device)
                out = model.generate(**inputs)
                cap = processor.decode(out[0], skip_special_tokens=True)

                # 4) Determine key
                elem_id = md.get("element_id") or getattr(el, "element_id", None) or el.id
                if not elem_id:
                    # fallback to type+count
                    if isinstance(el, UnstructuredImage):
                        elem_id = f"image_{img_count}"
                        img_count += 1
                    else:
                        elem_id = f"table_{tbl_count}"
                        tbl_count += 1

                # 5) Store in respective dict
                if isinstance(el, UnstructuredImage):
                    image_captions[elem_id] = cap
                else:
                    table_captions[elem_id] = cap

    return image_captions, table_captions

# -----------------------
# Example usage:
# docs = partition(..., extract_image_block_to_payload=True, extract_image_block_types=["Image","Table"])
img_caps, tbl_caps = generate_captions_from_memory(documents)
# print("Images:", img_caps)
# print("Tables:", tbl_caps)


In [28]:
img_caps

{'cff385ebc0b5f5a9c6ee1f0b8712f045': 'a whiteboard with a drawing of a tree and a line of numbers',
 '578876ea540ed862565bf7d09fe604b5': 'a cartoon drawing of two men sitting at a table',
 '68030cdafc9373bc09db590193bbf22c': 'a screenshote screen with the wordpress website',
 '68fd69ac28cc27945a75baf22aa67b93': 'the dw security screen',
 '913ad1e70018f732f5ed6e5d297032f5': 'the vulnerabilityrq injection button',
 'a5a80e7b29690ea5541fb1540399dae7': 'a screenshot of a computer screen with a text box',
 '4b1c36aa6c12872d20e2987c05d7a549': 'a screenshot of a code code with a red and blue background',
 '92dd5c1b93a5d478d4b57ab0487a5622': 'a white square with a black outline',
 'a48b7c351bd1c078516261534bbe16f8': 'a screenshot of a code with a red and blue background',
 'cc87ac3edf37602795fb37502e500313': 'a screenshot of a text editor',
 '221277e92b12daaba3c97227a7e43b16': 'a screenshote sign in the form of a sign in the form of a sign in the form',
 'f14ef2fc84069b4fe76211b270486b08': 'th

In [29]:
from typing import Any, Dict, List, Tuple
from unstructured.documents.elements import (
    Element,
    Image as UnstructuredImage,
    Table as UnstructuredTable,
    Text,
    Title,
    ListItem,
    NarrativeText,
)

# Define which classes count as “text”
TEXT_TYPES = (Text, Title, ListItem, NarrativeText)

def restructure_all_elements_flat(
    documents: List[Dict[str, Any]]
) -> Tuple[List[UnstructuredImage], List[UnstructuredTable], List[Element]]:
    """
    Flattens a list of parsed documents into three lists:
      1) all UnstructuredImage elements
      2) all UnstructuredTable elements
      3) all text-based elements (Text, Title, ListItem, NarrativeText)

    Args:
        documents: List of dicts, each with keys:
            - "filename": str
            - "elements": List[Element]

    Returns:
        Tuple of three lists: (all_images, all_tables, all_texts)
    """
    all_images: List[UnstructuredImage] = []
    all_tables: List[UnstructuredTable] = []
    all_texts: List[Element] = []

    for doc in documents:
        for el in doc.get("elements", []):
            if isinstance(el, UnstructuredImage):
                all_images.append(el)
            elif isinstance(el, UnstructuredTable):
                all_tables.append(el)
            elif isinstance(el, TEXT_TYPES):
                all_texts.append(el)
            # else: ignore other element types

    return all_images, all_tables, all_texts

# --------------------
# Example usage:

# Suppose you already have:
# documents = partition(..., extract_image_block_to_payload=True, extract_image_block_types=["Image","Table"])

all_images, all_tables, all_texts = restructure_all_elements_flat(documents)

print(f"Found {len(all_images)} images, {len(all_tables)} tables, {len(all_texts)} text elements.")
# You can now pass these into your captioning or LangChain conversion steps.


Found 27 images, 4 tables, 411 text elements.


**Get File from the Google Drive Folder link**

In [30]:
from typing import List, Dict, Any
from langchain.schema import Document
from unstructured.documents.elements import (
    Text,
    Title,
    ListItem,
    NarrativeText,
    Image as UnstructuredImage,
    Table as UnstructuredTable,
)

TEXT_TYPES = (Text, Title, ListItem, NarrativeText)

def convert_elements_to_langchain_docs(
    texts: List[Any],
    images: List[UnstructuredImage],
    tables: List[UnstructuredTable],
    image_captions: Dict[str, str],
    table_captions: Dict[str, str],
) -> List[Document]:
    """
    Build a unified list of LangChain Documents from text elements,
    image elements + captions, and table elements + captions.
    """
    docs: List[Document] = []

    # 1) Text elements → Documents
    for el in texts:
        docs.append(Document(
            page_content=el.text,
            metadata={
                "type": "text",
                "element_id": el.id,
                "source": getattr(el.metadata, "filename", None),
            },
        ))

    # 2) Image elements → caption Docs
    for el in images:
        el_dict = el.to_dict()
        elem_id = el_dict.get("id") or el.id
        caption = image_captions.get(elem_id, "")
        # skip if no caption
        if not caption:
            continue
        base64_str = el_dict.get("metadata", {}).get("image_base64")
        docs.append(Document(
            page_content=f"[IMAGE:{elem_id}] {caption}",
            metadata={
                "type": "image_caption",
                "element_id": elem_id,
                "image_base64": base64_str,
            },
        ))

    # 3) Table elements → caption Docs
    for el in tables:
        el_dict = el.to_dict()
        elem_id = el_dict.get("id") or el.id
        caption = table_captions.get(elem_id, "")
        if not caption:
            continue
        base64_str = el_dict.get("metadata", {}).get("image_base64")
        docs.append(Document(
            page_content=f"[TABLE:{elem_id}] {caption}",
            metadata={
                "type": "table_caption",
                "element_id": elem_id,
                "image_base64": base64_str,
            },
        ))

    return docs

# ----------------------
# EXAMPLE PIPELINE USAGE:

# 1) Flatten raw elements:
# all_images, all_tables, all_texts = restructure_all_elements_flat(documents)

# 2) Generate captions:
# img_caps, tbl_caps = generate_captions_from_memory(documents)

# 3) Convert to LangChain Documents:
lc_docs = convert_elements_to_langchain_docs(
     texts=all_texts,
     images=all_images,
     tables=all_tables,
     image_captions=img_caps,
     table_captions=tbl_caps,
 )

# 4) Ready for dynamic_chunk_documents(lc_docs) or embedding!


In [31]:
lc_docs

In [33]:
!pip install -U langchain-text-splitters


In [35]:
from typing import List
from langchain.schema import Document
from langchain.text_splitter import (
    CharacterTextSplitter,
    RecursiveCharacterTextSplitter,
    MarkdownTextSplitter,
    HTMLHeaderTextSplitter,
)
from langchain_text_splitters import RecursiveJsonSplitter


def get_splitter_for_type(doc_type: str):
    """
    Return the optimal TextSplitter for the given document type.
    """
    if doc_type == "markdown":
        # Splits at Markdown headings and paragraphs for coherent sections
        return MarkdownTextSplitter(chunk_size=512, chunk_overlap=64)  # :contentReference[oaicite:6]{index=6}
    if doc_type == "html":
        # Splits by HTML header tags, preserving section context
        return HTMLHeaderTextSplitter(
            headers_to_split_on=["h1", "h2", "h3"],
            chunk_size=800,
            chunk_overlap=100,
        )  # :contentReference[oaicite:7]{index=7}
    if doc_type == "json":
        # Recursively splits nested JSON objects into character‑bounded chunks
        return RecursiveJsonSplitter(max_chunk_size=500, min_chunk_size=100)  # :contentReference[oaicite:8]{index=8}
    if doc_type == "code":
        # Language‑aware splitting using syntax separators for code
        return RecursiveCharacterTextSplitter.from_language(
            "python", chunk_size=1000, chunk_overlap=200
        )  # :contentReference[oaicite:9]{index=9}
    # Fallback for plain text: fixed‑size character chunks with overlap
    return CharacterTextSplitter(chunk_size=1000, chunk_overlap=200)  # :contentReference[oaicite:10]{index=10}

def dynamic_chunk_documents(
    lc_docs: List[Document]
) -> List[Document]:
    """
    Apply document‑specific chunking to a list of LangChain Documents.

    Args:
        lc_docs: List of Documents, each with metadata["doc_type"] in
                 {"markdown", "html", "json", "code", "text"}.

    Returns:
        Flat list of smaller Document chunks.
    """
    all_chunks: List[Document] = []
    for doc in lc_docs:
        # Determine which splitter to use based on doc_type
        doc_type = doc.metadata.get("doc_type", "text").lower()
        splitter = get_splitter_for_type(doc_type)
        # Split the document into chunks
        chunks = splitter.split_documents([doc])  # :contentReference[oaicite:11]{index=11}
        # Annotate each chunk with its parent type for traceability
        for chunk in chunks:
            chunk.metadata["parent_doc_type"] = doc_type
            all_chunks.append(chunk)
    return all_chunks

# --------------------------
# Example usage:
#
# Assume `lc_docs` is your list of Documents already
# created from text, image captions, etc., each having
# metadata["doc_type"] ∈ {"markdown","html","json","code","text"}.
#
chunked_docs = dynamic_chunk_documents(lc_docs)
# print(f"Total chunks generated: {len(chunked_docs)}")
# for c in chunked_docs[:3]:
#     print(c.metadata["parent_doc_type"], "→", c.page_content[:100])


In [36]:
chunked_docs

[Document(metadata={'type': 'text', 'element_id': '5b3b94ca292ca586f4ce916786812023', 'source': '6-CNN.pptx', 'parent_doc_type': 'text'}, page_content='Deep Learning'),
 Document(metadata={'type': 'text', 'element_id': '3f31ef5726497874059ef81e77f3e5d2', 'source': '6-CNN.pptx', 'parent_doc_type': 'text'}, page_content='FFNN'),
 Document(metadata={'type': 'text', 'element_id': '9bdf81833853223a41f5e2c4c8361854', 'source': '6-CNN.pptx', 'parent_doc_type': 'text'}, page_content='CNN'),
 Document(metadata={'type': 'text', 'element_id': '97969b378389041191aa5bc4fc67c5b9', 'source': '6-CNN.pptx', 'parent_doc_type': 'text'}, page_content='Convolution'),
 Document(metadata={'type': 'text', 'element_id': 'c605f6e6cee055c07e68cc89d07e638e', 'source': '6-CNN.pptx', 'parent_doc_type': 'text'}, page_content='Feedforward neural networks (FNN)'),
 Document(metadata={'type': 'text', 'element_id': '0d148e4b96057949a34a0348e666a7b8', 'source': '6-CNN.pptx', 'parent_doc_type': 'text'}, page_content='In F

In [37]:
from langchain_community.embeddings import HuggingFaceEmbeddings

# Initialize the embedding model
embedding_model = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")


<ipython-input-37-eb309a9ed059>:4: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embedding_model = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.5k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [38]:
# Extract the text content from each document
texts = [doc.page_content for doc in chunked_docs]

# Generate embeddings for the texts
embeddings = embedding_model.embed_documents(texts)


In [39]:
embeddings

[[-0.10024536401033401,
  -0.04983586445450783,
  0.06778673082590103,
  0.004215051885694265,
  -0.047210466116666794,
  0.017139509320259094,
  -0.0022719278931617737,
  -0.017115913331508636,
  -0.02959001623094082,
  -0.1187131255865097,
  -0.03816599398851395,
  0.020351558923721313,
  -0.0148552767932415,
  0.034485120326280594,
  -0.11386056989431381,
  0.02793450653553009,
  0.040109794586896896,
  0.04308732971549034,
  -0.18421705067157745,
  -0.06481397151947021,
  -0.02552414871752262,
  -0.002184299984946847,
  -0.030128495767712593,
  -0.013696216978132725,
  0.06019113212823868,
  0.043445486575365067,
  0.032377518713474274,
  -0.011177696287631989,
  0.05878119915723801,
  -0.11659083515405655,
  0.08325421810150146,
  -0.03398315608501434,
  0.027385219931602478,
  0.05018635094165802,
  -0.06714402884244919,
  0.04789121821522713,
  -0.073893703520298,
  0.023334667086601257,
  0.03440704569220543,
  -0.0014689270174130797,
  -0.028689216822385788,
  -0.0385048612952

In [40]:
from langchain_community.vectorstores import Chroma

# Define the directory to persist the Chroma database
persist_directory = "./chroma_db"

# Create the Chroma vector store from documents
vector_store = Chroma.from_documents(
    documents=lc_docs,
    embedding=embedding_model,
    persist_directory=persist_directory
)

# Persist the vector store to disk
vector_store.persist()


<ipython-input-40-baddf4bc6ac0>:14: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  vector_store.persist()


In [41]:
# Define your query
query = "What are the CNN"

# Perform the similarity search
similar_docs = vector_store.similarity_search(query, k=5)

# Display the results
for doc in similar_docs:
    print(doc.page_content)


CNN
CNN
Why CNN
Inspiration for CNN
Inspiration for CNN


**loads the Documents of GDrive Folder**

**Download the GDrive File**

**Function to Generate Captions**